In [4]:
import pandas as pd
import plotly.express as px
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt


with open('./token.txt', 'r') as f:
    TOKEN = f.read()
    px.set_mapbox_access_token(TOKEN)

In [5]:
df = pd.read_parquet('../data/fires_merged_comunas.parquet')
df['acq_date'] = pd.to_datetime(df['acq_date'])

In [7]:
a = df.copy()
a['year'] = a['acq_date'].dt.year
a['month'] = a['acq_date'].dt.month
a['day'] = a['acq_date'].dt.day
a = a[a['year'] == 2017]
a = a.groupby(['latitude', 'longitude', 'confidence', 'track', 'acq_date'])['frp'].mean().reset_index()
a = a.sort_values(by='acq_date', ascending=True)
fig = px.scatter_mapbox(a, lat="latitude", lon="longitude", animation_frame='acq_date', color="frp", zoom=3, title='Wildfires', range_color=[0, 1000], color_continuous_scale='reds')
fig.update_layout(mapbox_style='satellite', title='Wildfires', height=800)
fig.show()

/home/stare/anaconda3/envs/ds/lib/python3.10/site-packages/plotly/express/_core.py:1979: FutureWarning:

When grouping with a length-1 list-like, you will need to pass a length-1 tuple to get_group in a future version of pandas. Pass `(name,)` instead of `name` to silence this warning.



In [13]:
# Process points grouped by day with DBSCAN to find clusters
from sklearn.cluster import DBSCAN
import geopandas as gpd

a = df.copy()
a['year'] = a['acq_date'].dt.year
a['month'] = a['acq_date'].dt.month
a['day'] = a['acq_date'].dt.day
a = a[a['year'] == 2017]
a = a.groupby(['latitude', 'longitude', 'acq_date'])['frp'].mean().reset_index()
a = a.sort_values(by='acq_date', ascending=True)

X = a[['latitude', 'longitude']].values
db = DBSCAN(eps=0.1, min_samples=10).fit(X)
a['cluster'] = db.labels_


ValueError: Cannot subset columns with a tuple with more than one element. Use a list instead.